In [125]:
from elastic_nerf.utils import wandb_utils as wu
from pathlib import Path
import pandas as pd
from IPython.display import display
from collections import defaultdict
import math
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

sweep_mappings = {
    # "2uxektzo": "ngp_occ-mipnerf360-baseline",
    # "kebumdc0": "ngp_occ-mipnerf360-baseline",
    # "xxjsfkbw": "ngp_prop-mipnerf360-baseline",
    # "8w0wks0x": "ngp_prop-mipnerf360-baseline",
    "qfkjdvv2": "ngp_occ-mipnerf360-sampling_single",
    "hy03dx0e": "ngp_occ-mipnerf360-sampling",
    "wsxh6gjo": "ngp_prop-mipnerf360-sampling",
    "8ishbvau": "ngp_prop-mipnerf360-sampling_single",
    # "b674pjcs": "ngp_occ-mipnerf360-baseline_head_depth1",
    # "58hgroe5": "ngp_prop-mipnerf360-baseline_head_depth1",
    # "c6g1mc5g": "ngp_occ-mipnerf360-baseline-mup",
    # "ccrwhsr5": "ngp_prop-mipnerf360-baseline-mup",
}

# TR1c_MRL_Sampling
This experiment tries to evaluate the performance of the Nerfacc NGP Occ and Nerfacc Prop models after training them in the style of Matroyshka Representation Learning (MRL), similar to the work presented in Matformer. Since the `Counter` scene seemed to have a noticeable decline for smaller width performance (without having any weird massive reductions), we do all of our experiments on this scene. Similar to before, we sample exponentially spaced widths of $d={64, 32, 16, 8}$ (with $d=64$ being the baseline full-width). However, unlike the previous two experiments where we train for all steps with the same width, we now experiment with 3 different training strategies and try to understand how this affects the final evaluation performance at 20k steps. Specifically, we change the number of widths that are sampled at each step (_subsampling_ in `Matformer` parlance), we change the sampling strategy (one of our proposals), and we change the loss weighting strategy. Recall that in Matformer, they found that joint optimization of all widths at every step was the best strategy, and that it did even better when paired with their proposed loss weighting strategy of $\sqrt{8} : \sqrt{4} : \sqrt{2} : \sqrt{1}$ for $d={256, 128, 64, 32}$ respectively. They note that:
> We find that all strategies that upweight the loss for the largest granularity perofrm well, with modest degradation on the M and S granularities.

## Subsampling
Recall that we have 4 exponentially spaced widths to sample from. It is not clear from the Matformer paper whether it is strictly necessary to jointly optimize across all widths at every step. Ideally, if we can come up with a way to just sample 1 width at every step, we can significantly accelerate the overall training speed since the amortized cost of sampling one of 4 widths is much lower than training the full width model at every step. Thus, for this experiment, we explore sampling either 1, 2, 3, or 4 (joint optimization) widths at every step. 

## Sampling Strategy
Matformer tries either joint optimization across all widths, or for the case of subsampling, they sample uniformly at random. We experiment with additional sampling strategies where we explore the impact of upweighting and downweighting the probability of sampling the largest widths. We hypothesize that if larger widths are sampled with a higher probability, the performance of the largest elastic width will approach the performance of the baseline full-width model, whereas the performance of the smallest elastic width would be worse than the performance of the baseline smallest-width model. Given that we can also weight the losses, it is unclear how the interaction between these two variables will affect the overall performance of each width.

## Loss Weighting Strategy
Similar to Matformer, we experiment with using a uniformly weighted loss for all sampled granularities, as well as trying to upweight and downweight the losses. Note that actual loss weight ratios are defined across all granularities, but since we also experiment with subsampling, this means that the actual loss weight ratios applied to a granularity at each step may be different since we normalize all the sampled loss weights to sum to 1. 

In [126]:
tables = ["EvalResultsSummarytable"]
sweeps = sweep_mappings.keys()
results_cache_dir = Path("/home/user/shared/results/elastic-nerf")
sweep_results = {}

for sweep in sweeps:
    sweep_results[sweep] = wu.fetch_sweep_results(
        sweep=sweep,
        refresh_cache=False,
        download_history=True,
        tables=tables,
        results_cache_dir=results_cache_dir,
    )
all_history = []
# Create a dataframe with all the results
for sweep_name in sweep_results:
    for run in sweep_results[sweep_name]:
        # Flatten the config
        flat_config = wu.flatten_dict(run.config, sep="-")
        # Concatenate the config with each row of the history results
        # Note that history results are already a dataframe
        history = run.history
        history["sweep_id"] = sweep_name
        history["run_id"] = run.run_id
        history["model_type"] = (
            "Nerfacc Prop" if "prop" in sweep_mappings[sweep_name] else "Nerfacc Occ"
        )
        history["sweep_name"] = sweep_mappings[sweep_name]
        for key in flat_config:
            try:
                history[key] = str(flat_config[key])
            except:
                print(f"Failed to add {key} to history with value {flat_config[key]}")
                raise
        all_history.append(history)

# %%
# Concatenate all the history results into a single dataframe
final_df = pd.concat(all_history, ignore_index=True)


# %%
fp = f"results_tr1c_mrl_sampling.csv"
final_df.to_csv(fp, index=False)
print(f"Saved results to {fp}")
df = pd.read_csv(fp)

(gonas) [WARNING] Using cached results for sweep qfkjdvv2
(gonas) [WARNING] Using cached results for sweep hy03dx0e
(gonas) [WARNING] Using cached results for sweep wsxh6gjo


(gonas) [WARNING] Using cached results for sweep 8ishbvau


Saved results to results_tr1c_mrl_sampling.csv


/tmp/ipykernel_2250064/1009082144.py:46: DtypeWarning: Columns (206,208,216,220,221) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(fp)


# Results
## Sampling Strategy
First, let's take a look at the different sampling strategies we explored.

In [127]:
print(sorted(df["sampling_strategy"].unique()))

['exp', 'exp-reverse', 'sequential', 'uniform']


When subsampling or jointly optimizing across 1,2,3 or 4 granularities, we explored the following sampling strategies:
1. Uniform: Sample uniformly at random
2. Exp-Reverse: Sample widths with probability proportional to their exponential spacing while upweighting the largest width

    $e^i$ for $i \in \{3,2,1,0\} \Longleftrightarrow \{20.09, 7.39, 2.71, 1.0\}  \to \{8, 16, 32, 64 \} $

When subsampling a single granularity at each step, we additionally explored:
1. Uniform: ...
2. Exp-Reverse: ...
3. Exp: Sample widths with probability proportional to their exponential spacing while downweighting the largest width

    $e^i$ for $i \in \{0,1,2,3\} \Longleftrightarrow \{1.0, 2.71, 7.39, 20.09\}  \to \{64, 32, 16, 8\}$

4. Sequential: Sample the granularities in order of decreasing width before cycling back to the largest width (and repeating). Over the course of training, this means that the number of times a granularity gets sampled will be $1/N$ (so similar to the uniform strategy), except that in this case, the order of sampling is fixed.

### Joint Optimization (4 granularities)
First, lets look at the performance of the different sampling strategies, when jointly optimizing across all 4 widths at each step, while varying the `loss_weight_strategy`. The key takeaway is that regardless of which strategy we use, the performance drop compared to the baseline is quite significant. Additionally, the performance of the sampling strategy is not consistent across different models (and from previous experiments, it's also not consistent across scenes).

In [128]:
num_scenes = len(df["scene"].unique())
table_cols = [
    "Sampling Strategy",
    "Loss Weight Strategy",
    "Width 64",
    "Width 64 %Err",
    "Width 32",
    "Width 32 %Err",
    "Width 16",
    "Width 16 %Err",
    "Width 8",
    "Width 8 %Err",
]
base_psnrs = {
    "Nerfacc Occ": {64: 26.78, 32: 26.67, 16: 26.19, 8: 25.58},
    "Nerfacc Prop": {64: 26.78, 32: 26.22, 16: 25.34, 8: 25.10},
}
dims = [64, 32, 16, 8]
for i, (model_type, model_group) in enumerate(df.groupby(by="model_type")):
    query = "_step == 20000 and `radiance_field-use_elastic_head` == True and `num_widths_to_sample` == 4"
    if model_type == "Nerfacc Prop":
        query += " and `density_field-use_elastic` == True"
    model_group = model_group.query(query)
    table_data = []
    for j, (sampling_strategy, sampling_strategy_group) in enumerate(
        model_group.groupby(by="sampling_strategy")
    ):
        for k, (loss_weight_strategy, loss_weight_strategy_group) in enumerate(
            sampling_strategy_group.groupby(by="loss_weight_strategy")
        ):
            table_row = {
                "Sampling Strategy": sampling_strategy.capitalize(),
                "Loss Weight Strategy": loss_weight_strategy.capitalize(),
            }
            for dim in dims:
                base_psnr = base_psnrs[model_type][dim]
                psnr_col = f"Eval Results Summary/psnr_avg/elastic_{dim}"
                psnr_avg = loss_weight_strategy_group[psnr_col].iloc[0]
                pc_diff = 100 * (psnr_avg - base_psnr) / base_psnr
                table_row.update({f"Width {dim}": f"{psnr_avg:.2f}"})
                table_row.update({f"Width {dim} %Err": f"{pc_diff:.2f}"})
            table_data.append(table_row)

    table_data = pd.DataFrame(table_data, columns=table_cols).sort_values(
        by="Width 64 %Err"
    )
    caption = f"Sampling strategy vs. Loss Weight strategy PSNR average performance when jointly optimizing 4 granularities ({model_type}) model."
    table_data = table_data.style.set_caption(caption)
    display(table_data)
    # print(
    #     table_data.to_latex(
    #         index=False,
    #         caption=f"Baseline performance (PSNR) after 20k steps of training for {model_type} model at different widths across scenes from the MipNeRF-360 dataset",
    #         label=f"tab:baseline_{model_type.replace(' ', '_')}",
    #         position="h",
    #         column_format="lcccccc",
    #         escape=True,
    #         bold_rows=True,
    #     )
    # )

Now let's look at the results once we subsample 2 or 3 granularities at each step. We can see that there is not much difference in performance between weighting the loss using `exp` vs. `exp-inv`. This makes sense because after normalizing the loss weights, the actual loss weight applied to each granularity is the same. So that being said, let's discard the `exp-inv` strategy, and only focus on the `uniform`, `exp`, and `matroyshka` strategies for the rest of the analysis.

In [129]:
num_scenes = len(df["scene"].unique())
table_cols = [
    "Sampling Strategy",
    "Loss Weight Strategy",
    "Num Widths to Subsample",
    "Width 64",
    "Width 64 %Err",
    "Width 32",
    "Width 32 %Err",
    "Width 16",
    "Width 16 %Err",
    "Width 8",
    "Width 8 %Err",
]
base_psnrs = {
    "Nerfacc Occ": {64: 26.78, 32: 26.67, 16: 26.19, 8: 25.58},
    "Nerfacc Prop": {64: 26.78, 32: 26.22, 16: 25.34, 8: 25.10},
}
dims = [64, 32, 16, 8]
for i, (model_type, model_group) in enumerate(df.groupby(by="model_type")):
    query = "_step == 20000 and `radiance_field-use_elastic_head` == True and `num_widths_to_sample` != 1"
    if model_type == "Nerfacc Prop":
        query += " and `density_field-use_elastic` == True"
    model_group = model_group.query(query)
    model_name_split = [m.capitalize() for m in model_type.split("_")]
    model_name_split[0] = model_name_split[0].upper()
    table_data = []
    for j, (sampling_strategy, sampling_strategy_group) in enumerate(
        model_group.groupby(by="sampling_strategy")
    ):
        for k, (loss_weight_strategy, loss_weight_strategy_group) in enumerate(
            sampling_strategy_group.groupby(by="loss_weight_strategy")
        ):
            for l, (num_widths_to_sample, num_widths_to_sample_group) in enumerate(
                loss_weight_strategy_group.groupby(by="num_widths_to_sample")
            ):
                table_row = {
                    "Sampling Strategy": sampling_strategy.capitalize(),
                    "Loss Weight Strategy": loss_weight_strategy.capitalize(),
                    "Num Widths to Subsample": num_widths_to_sample,
                }
                for dim in dims:
                    base_psnr = base_psnrs[model_type][dim]
                    psnr_col = f"Eval Results Summary/psnr_avg/elastic_{dim}"
                    psnr_avg = num_widths_to_sample_group[psnr_col].iloc[0]
                    pc_diff = 100 * (psnr_avg - base_psnr) / base_psnr
                    table_row.update(
                        {f"Width {dim}": f"{psnr_avg:.2f} ({pc_diff:.2f})%"}
                    )
                    table_row.update({f"Width {dim} %Err": f"{pc_diff:.2f}"})
                table_data.append(table_row)

    table_data = pd.DataFrame(table_data, columns=table_cols).sort_values(
        by=["Num Widths to Subsample", "Width 64 %Err"]
    )
    table_data.drop(
        columns=["Width 64 %Err", "Width 32 %Err", "Width 16 %Err", "Width 8 %Err"],
        inplace=True,
    )
    caption = f"Sampling strategy vs. Loss Weight strategy PSNR average performance when jointly optimizing 4 granularities ({model_type}) model."
    table_data_style = table_data.style.set_caption(caption)
    table_data["Strategy Pair"] = (
        table_data["Sampling Strategy"] + " + " + table_data["Loss Weight Strategy"]
    )

    # Convert PSNR average values to numeric if they're not already
    for width in ["Width 64", "Width 32", "Width 16", "Width 8"]:
        table_data[width] = table_data[width].apply(lambda x: float(x.split(" ")[0]))

    # Define the widths to iterate over
    widths = ["Width 64", "Width 32", "Width 16", "Width 8"]

    # Set up the matplotlib figure for 2x2 subplots
    fig, axes = plt.subplots(2, 2, figsize=(20, 16))
    axes = axes.flatten()  # Flatten to easily index them

    # Loop through each width and plot a heatmap in each subplot
    for i, width in enumerate(widths):
        # Prepare the data for the heatmap
        heatmap_data = table_data.pivot(
            index="Num Widths to Subsample", columns="Strategy Pair", values=width
        )

        # Plot the heatmap
        sns.heatmap(
            heatmap_data,
            ax=axes[i],
            annot=True,
            fmt=".2f",
            cmap="viridis",
            linewidths=0.5,
        )

        # Set the title for each subplot
        axes[i].set_title(f"Performance (PSNR) for {model_type} model ({width}) ")
        axes[i].set_xlabel("Sampling Strategy + Loss Weight Strategy Pair")
        axes[i].set_ylabel("Num Widths to Subsample")

    # Adjust layout to prevent overlap
    plt.tight_layout()

    # Display the plot
    plt.show()
    display(table_data_style)
    # print(
    #     table_data.to_latex(
    #         index=False,
    #         caption=caption,
    #         label=f"tab:tr1c_mrl_sampling_strategy{model_type.replace(' ', '_')}",
    #         position="h",
    #         column_format="lcccccc",
    #         escape=True,
    #         bold_rows=True,
    #     )
    # )

The following heatmaps show the percent error in performance of the Nerfacc Occ and Nerfacc Prop with the following configurations vs. the baseline models at the corresponding widths:
1. Varying the number of granularities sampled at each step $N \in \{2,3,4\}$
2. Varying the sampling strategy $S \in \{\text{uniform}, \text{exp}, \text{matroyshka}\}$
3. Varying the loss weighting strategy $\mathcal{L} \in \{\text{uniform}, \text{exp}, \text{matroyshka}\}$

As expected, we can see that larger widths do better when sampled more frequently, while smaller widths do worse. This trend is somewhat consistent across both Nerfacc Occ and Nerfacc Prop models. However, it is difficult to come to a robust conclusion regarding the subsampling strategy. While one might expect that jointly sampling all granularities would work best, it appears that for both Width 64 and 32, sampling 2 granularities performs better on average. Even when doing uniform sampling with uniform loss-weightage, sampling 2 granularities performs better than sampling 3 or 4 granularities. This is quite surprising, and it is unclear why this is the case. Also interesting to note is that subsampling 1 width with a sampling probability that upweights the largest width results in much better performance for the largest granularity, and is in fact better than jointly optimizing across all 4 granularities. This shows that there may be some promise in subsampling with just a single granularity, _if_ we can figure out the reason behind why the training dynamics behave the way they do.

In [130]:
num_scenes = len(df["scene"].unique())
table_cols = [
    "Sampling Strategy",
    "Loss Weight Strategy",
    "Num Widths to Subsample",
    "Width 64",
    "Width 64 %Err",
    "Width 32",
    "Width 32 %Err",
    "Width 16",
    "Width 16 %Err",
    "Width 8",
    "Width 8 %Err",
]
base_psnrs = {
    "Nerfacc Occ": {64: 26.78, 32: 26.67, 16: 26.19, 8: 25.58},
    "Nerfacc Prop": {64: 26.78, 32: 26.22, 16: 25.34, 8: 25.10},
}
dims = [64, 32, 16, 8]
for i, (model_type, model_group) in enumerate(df.groupby(by="model_type")):
    query = "_step == 20000 and `radiance_field-use_elastic_head` == True"
    if model_type == "Nerfacc Prop":
        query += " and `density_field-use_elastic` == True"
    model_group = model_group.query(query)
    table_data = []
    for j, (sampling_strategy, sampling_strategy_group) in enumerate(
        model_group.groupby(by="sampling_strategy")
    ):
        if sampling_strategy in ["exp", "sequential"]:
            continue
        for k, (loss_weight_strategy, loss_weight_strategy_group) in enumerate(
            sampling_strategy_group.groupby(by="loss_weight_strategy")
        ):
            if loss_weight_strategy == "exp-inv":
                continue

            for l, (num_widths_to_sample, num_widths_to_sample_group) in enumerate(
                loss_weight_strategy_group.groupby(by="num_widths_to_sample")
            ):
                table_row = {
                    "Sampling Strategy": sampling_strategy.capitalize(),
                    "Loss Weight Strategy": loss_weight_strategy.capitalize(),
                    "Num Widths to Subsample": num_widths_to_sample,
                }
                for dim in dims:
                    base_psnr = base_psnrs[model_type][dim]
                    psnr_col = f"Eval Results Summary/psnr_avg/elastic_{dim}"
                    psnr_avg = num_widths_to_sample_group[psnr_col].iloc[0]
                    pc_diff = 100 * (psnr_avg - base_psnr) / base_psnr
                    # table_row.update(
                    #     {f"Width {dim}": f"{psnr_avg:.2f} ({pc_diff:.2f})%"}
                    # )
                    # table_row.update({f"Width {dim} %Err": f"{pc_diff:.2f}"})
                    table_row.update({f"Width {dim}": f"{pc_diff:.2f}"})
                table_data.append(table_row)

    table_data = pd.DataFrame(table_data, columns=table_cols).sort_values(
        by=["Num Widths to Subsample", "Width 64 %Err"]
    )
    # table_data.drop(
    #     columns=["Width 64 %Err", "Width 32 %Err", "Width 16 %Err", "Width 8 %Err"],
    #     inplace=True,
    # )
    caption = f"Sampling strategy vs. Loss Weight strategy PSNR average performance when jointly optimizing 4 granularities ({model_type}) model."
    table_data_style = table_data.style.set_caption(caption)
    table_data["Strategy Pair"] = (
        table_data["Sampling Strategy"] + " + " + table_data["Loss Weight Strategy"]
    )

    # Convert PSNR average values to numeric if they're not already
    for width in ["Width 64", "Width 32", "Width 16", "Width 8"]:
        table_data[width] = table_data[width].apply(lambda x: float(x.split(" ")[0]))

    # Define the widths to iterate over
    widths = ["Width 64", "Width 32", "Width 16", "Width 8"]

    # Set up the matplotlib figure for 2x2 subplots
    fig, axes = plt.subplots(2, 2, figsize=(20, 16))
    axes = axes.flatten()  # Flatten to easily index them

    # Loop through each width and plot a heatmap in each subplot
    for i, width in enumerate(widths):
        # Prepare the data for the heatmap
        heatmap_data = table_data.pivot(
            index="Num Widths to Subsample", columns="Strategy Pair", values=width
        )

        # Plot the heatmap
        sns.heatmap(
            heatmap_data,
            ax=axes[i],
            annot=True,
            fmt=".2f",
            cmap="viridis",
            linewidths=0.5,
        )

        # Set the title for each subplot
        axes[i].set_title(f"Performance (PSNR) for {model_type} model ({width}) ")
        axes[i].set_xlabel("Sampling Strategy + Loss Weight Strategy Pair")
        axes[i].set_ylabel("Num Widths to Subsample")

    # Adjust layout to prevent overlap
    plt.tight_layout()

    # Display the plot
    plt.show()
    # display(table_data_style)
    # print(
    #     table_data.to_latex(
    #         index=False,
    #         caption=caption,
    #         label=f"tab:tr1c_mrl_sampling_strategy{model_type.replace(' ', '_')}",
    #         position="h",
    #         column_format="lcccccc",
    #         escape=True,
    #         bold_rows=True,
    #     )
    # )

Lastly, let's take a closer look at just subsampling 1 granularity.

In [131]:
num_scenes = len(df["scene"].unique())
table_cols = [
    "Sampling Strategy",
    "Loss Weight Strategy",
    "Num Widths to Subsample",
    "Width 64",
    "Width 64 %Err",
    "Width 32",
    "Width 32 %Err",
    "Width 16",
    "Width 16 %Err",
    "Width 8",
    "Width 8 %Err",
]
base_psnrs = {
    "Nerfacc Occ": {64: 26.78, 32: 26.67, 16: 26.19, 8: 25.58},
    "Nerfacc Prop": {64: 26.78, 32: 26.22, 16: 25.34, 8: 25.10},
}
dims = [64, 32, 16, 8]
for i, (model_type, model_group) in enumerate(df.groupby(by="model_type")):
    query = "_step == 20000 and `radiance_field-use_elastic_head` == True"
    if model_type == "Nerfacc Prop":
        query += " and `density_field-use_elastic` == True"
    model_group = model_group.query(query)
    table_data = []
    for j, (sampling_strategy, sampling_strategy_group) in enumerate(
        model_group.groupby(by="sampling_strategy")
    ):
        for k, (loss_weight_strategy, loss_weight_strategy_group) in enumerate(
            sampling_strategy_group.groupby(by="loss_weight_strategy")
        ):
            for l, (num_widths_to_sample, num_widths_to_sample_group) in enumerate(
                loss_weight_strategy_group.groupby(by="num_widths_to_sample")
            ):
                if num_widths_to_sample != 1:
                    continue
                table_row = {
                    "Sampling Strategy": sampling_strategy.capitalize(),
                    "Loss Weight Strategy": loss_weight_strategy.capitalize(),
                    "Num Widths to Subsample": num_widths_to_sample,
                }
                for dim in dims:
                    base_psnr = base_psnrs[model_type][dim]
                    psnr_col = f"Eval Results Summary/psnr_avg/elastic_{dim}"
                    psnr_avg = num_widths_to_sample_group[psnr_col].iloc[0]
                    pc_diff = 100 * (psnr_avg - base_psnr) / base_psnr
                    # table_row.update(
                    #     {f"Width {dim}": f"{psnr_avg:.2f} ({pc_diff:.2f})%"}
                    # )
                    # table_row.update({f"Width {dim} %Err": f"{pc_diff:.2f}"})
                    table_row.update({f"Width {dim}": f"{pc_diff:.2f}"})
                table_data.append(table_row)

    table_data = pd.DataFrame(table_data, columns=table_cols).sort_values(
        by=["Num Widths to Subsample", "Width 64 %Err"]
    )
    # table_data.drop(
    #     columns=["Width 64 %Err", "Width 32 %Err", "Width 16 %Err", "Width 8 %Err"],
    #     inplace=True,
    # )
    caption = f"Sampling strategy vs. Loss Weight strategy PSNR average performance when jointly optimizing 4 granularities ({model_type}) model."
    table_data_style = table_data.style.set_caption(caption)

    # Convert PSNR average values to numeric if they're not already
    for width in ["Width 64", "Width 32", "Width 16", "Width 8"]:
        table_data[width] = table_data[width].apply(lambda x: float(x.split(" ")[0]))

    # Define the widths to iterate over
    widths = ["Width 64", "Width 32", "Width 16", "Width 8"]

    # Set up the matplotlib figure for 2x2 subplots
    fig, axes = plt.subplots(2, 2, figsize=(20, 16))
    axes = axes.flatten()  # Flatten to easily index them

    # Loop through each width and plot a heatmap in each subplot
    for i, width in enumerate(widths):
        # Prepare the data for the heatmap
        heatmap_data = table_data.pivot(
            index="Sampling Strategy", columns="Loss Weight Strategy", values=width
        )

        # Plot the heatmap
        sns.heatmap(
            heatmap_data,
            ax=axes[i],
            annot=True,
            fmt=".2f",
            cmap="viridis",
            linewidths=0.5,
        )

        # Set the title for each subplot
        axes[i].set_title(f"Performance (PSNR) for {model_type} model ({width}) ")
        axes[i].set_xlabel("Loss Weight Strategy")
        axes[i].set_ylabel("Sampling Strategy")

    # Adjust layout to prevent overlap
    plt.tight_layout()

    # Display the plot
    plt.show()
    # display(table_data_style)
    # print(
    #     table_data.to_latex(
    #         index=False,
    #         caption=caption,
    #         label=f"tab:tr1c_mrl_sampling_strategy{model_type.replace(' ', '_')}",
    #         position="h",
    #         column_format="lcccccc",
    #         escape=True,
    #         bold_rows=True,
    #     )
    # )

In [132]:
num_scenes = len(df["scene"].unique())
table_cols = ["Sampling Strategy", "Width 64", "Width 32", "Width 16", "Width 8"]
base_psnrs = {
    "Nerfacc Occ": {64: 26.78, 32: 26.67, 16: 26.19, 8: 25.58},
    "Nerfacc Prop": {64: 26.78, 32: 26.22, 16: 25.34, 8: 25.10},
}
dims = [64, 32, 16, 8]
for i, (model_type, model_group) in enumerate(df.groupby(by="model_type")):
    query = "_step == 20000 and `radiance_field-use_elastic_head` == True and `num_widths_to_sample` == 4"
    if model_type == "Nerfacc Prop":
        query += " and `density_field-use_elastic` == True"
    model_group = model_group.query(query)
    table_data = []
    for j, (sampling_strategy, sampling_strategy_group) in enumerate(
        model_group.groupby(by="sampling_strategy")
    ):
        table_row = {"Sampling Strategy": sampling_strategy.capitalize()}
        for dim in dims:
            base_psnr = base_psnrs[model_type][dim]
            psnr_col = f"Eval Results Summary/psnr_avg/elastic_{dim}"
            psnr_avg = sampling_strategy_group[psnr_col].mean()
            psnr_std = sampling_strategy_group[psnr_col].std()
            pc_diff = 100 * (psnr_avg - base_psnr) / base_psnr
            table_row.update(
                {f"Width {dim}": f"{psnr_avg:.2f}±{psnr_std:.2f} ({pc_diff:.2f}%)"}
            )
        table_data.append(table_row)

    table_data = pd.DataFrame(table_data, columns=table_cols)
    caption = f"Average performance of a sampling strategy across different loss_weight_strategies when jointly optimizing 4 granularities ({model_type}) model."
    table_data = table_data.style.set_caption(caption)
    display(table_data)
    # print(
    #     table_data.to_latex(
    #         index=False,
    #         caption=f"Baseline performance (PSNR) after 20k steps of training for {model_type} model at different widths across scenes from the MipNeRF-360 dataset",
    #         label=f"tab:baseline_{model_type.replace(' ', '_')}",
    #         position="h",
    #         column_format="lcccccc",
    #         escape=True,
    #         bold_rows=True,
    #     )
    # )

In [133]:
def get_loss_weight(elastic_width, loss_weight_strategy, num_widths_to_sample):
    matroyshka_weights_map = {
        8: 1,
        16: math.sqrt(2),
        32: 2,
        64: math.sqrt(8),
    }
    matroyshka_inv_weights_map = {
        8: 1.0 / math.sqrt(8),
        16: 1.0 / 2.0,
        32: 1.0 / math.sqrt(2),
        64: 1.0,
    }
    exp_weights = [math.exp(i) for i in range(4)]
    widths = [8, 16, 32, 64]
    exp_weights_map = {width: weight for width, weight in zip(widths, exp_weights)}
    exp_inv_weights_map = {
        width: 1.0 / weight for width, weight in zip(widths, reversed(exp_weights))
    }
    if loss_weight_strategy == "uniform":
        return 1 / num_widths_to_sample
    elif loss_weight_strategy == "uniform-inv":
        return 1
    elif loss_weight_strategy == "matroyshka":
        return matroyshka_weights_map[int(elastic_width)]
    elif loss_weight_strategy == "matroyshka-inv":
        return matroyshka_inv_weights_map[int(elastic_width)]
    elif loss_weight_strategy == "exp":
        return exp_weights_map[int(elastic_width)]
    elif loss_weight_strategy == "exp-inv":
        return exp_inv_weights_map[int(elastic_width)]
    else:
        raise ValueError(f"Invalid loss weight strategy: {loss_weight_strategy}")


# Print out the resulting loss weights for the combination of each strategy, width and num_widths_to_sample
loss_weight_strategies = [
    "uniform",
    "uniform-inv",
    "matroyshka",
    "matroyshka-inv",
    "exp",
    "exp-inv",
]
table_data = []
table_cols = [
    "Loss Weight Strategy",
    "Width 64",
    "Width 32",
    "Width 16",
    "Width 8",
]
for loss_weight_strategy in loss_weight_strategies:
    for num_widths_to_sample in [4, 3, 2, 1]:
        table_row = {
            "Loss Weight Strategy": loss_weight_strategy,
        }
        sum = 0
        loss_weights = []
        for elastic_width in [64, 32, 16, 8]:
            loss_weight = get_loss_weight(
                elastic_width, loss_weight_strategy, num_widths_to_sample
            )
            loss_weights.append(loss_weight)
            sum += loss_weight
        for i, elastic_width in enumerate([64, 32, 16, 8]):
            loss_weight = loss_weights[i] / sum
            table_row.update(
                {
                    f"Width {elastic_width}": f"{loss_weight:.3f}",
                }
            )
        table_data.append(table_row)

table_data = pd.DataFrame(table_data, columns=table_cols)
table_data.sort_values(by=["Loss Weight Strategy"], inplace=True)
table_data

Loss Weight Strategy Width 64 Width 32 Width 16 Width 8
19                  exp    0.644    0.237    0.087   0.032
18                  exp    0.644    0.237    0.087   0.032
17                  exp    0.644    0.237    0.087   0.032
16                  exp    0.644    0.237    0.087   0.032
23              exp-inv    0.644    0.237    0.087   0.032
21              exp-inv    0.644    0.237    0.087   0.032
20              exp-inv    0.644    0.237    0.087   0.032
22              exp-inv    0.644    0.237    0.087   0.032
10           matroyshka    0.391    0.276    0.195   0.138
11           matroyshka    0.391    0.276    0.195   0.138
8            matroyshka    0.391    0.276    0.195   0.138
9            matroyshka    0.391    0.276    0.195   0.138
12       matroyshka-inv    0.391    0.276    0.195   0.138
13       matroyshka-inv    0.391    0.276    0.195   0.138
14       matroyshka-inv    0.391    0.276    0.195   0.138
15       matroyshka-inv    0.391    0.276    0.195   0.138
3               uniform    0.250    0.250    0.250   0.250
2               uniform    0.250    0.250    0.250   0.250
1               uniform    0.250    0.250    0.250   0.250
0               uniform    0.250    0.250    0.250   0.250
7           uniform-inv    0.250    0.250    0.250   0.250
6           uniform-inv    0.250    0.250    0.250   0.250
5           uniform-inv    0.250    0.250    0.250   0.250
4           uniform-inv    0.250    0.250    0.250   0.250